In [1]:
import thinkdsp
import pygame,easygui
def sample_generator():
    #The Wave is Segmentet into Sequences (0.1 sec)
    GotIt = False
    while not GotIt :
        try :
            M_Name = easygui.enterbox("Enter .wav File(Name)","Music Import")
            if not ".wav" in M_Name :

                M_Name += ".wav"
            wave = thinkdsp.read_wave(M_Name)
            GotIt = True
        except:
            easygui.msgbox("Failed to load wav-File","Loading Error")
    start = 0.0
    Cash = []
    Cash2 = []
    Meng = 0
    while start < wave.duration:
        segment = wave.segment(start, 0.1)
        if segment.duration > 0:
            Meng += 1
            spectrum = segment.make_spectrum()
            Cash.append(spectrum)
            Cash2.append(segment)
        start += 0.1
    return Cash,Cash2,Meng,M_Name

In [2]:
def GraphDraw():
    global Freq_List
    SCREENHEIGHT = screen.get_height()
    Itera = 0
    HEIGH = 0
    for Var in Freq_List :
        if Var > HEIGH :
            HEIGH = Var
    for Item in Freq_List :
        try :
            pygame.draw.line(screen,[0,100,0],Old,[Itera*5,(SCREENHEIGHT-HEIGH)+Item])
        except :
            pass
        Old = [Itera*5,(SCREENHEIGHT-HEIGH)+Item]
        print(SCREENHEIGHT,(SCREENHEIGHT-HEIGH)+Item)
        Itera += 1
    

In [3]:
def Render(screen,Bars,fs):
    #Peak Scanner
    SID = -1
    GR = 0
    GrID = 0
    for Bar in Bars :
            SID += 1
            if Bar[3] > GR :
                GR = Bar[3]
                GrID = SID
                Hfs = fs[GrID]
    #Main Render
    D = 5
    Len = len(Bars)
    global Epics_Cash
    ID = -1
    #Blue Line 
    if Line_Aktiv :
        for Bar in Bars :
            try :
                pygame.draw.line(screen,[0,100,100],Graph,[Bar[0]-1,Bar[3]+30],3)
                pygame.draw.line(screen,[0,100,100],[Bar[0]-1,Bar[3]+30],[Bar[0]+D+1,Bar[3]+30],3)
            except :
                pass
            Graph = [Bar[0]+D+1,Bar[3]+30] 
    #Graph
    if Bar_Aktiv :
        for Bar in Bars :
            #Bar[1]+=20
            ID += 1
            if ID == Epics_Cash[0]:
                pygame.draw.rect(screen,Epics_Cash[3],Bar)
            elif ID-1 == Epics_Cash[0] or ID+1 == Epics_Cash[0]:
                pygame.draw.rect(screen,Epics_Cash[2],Bar)
            else :
                pygame.draw.rect(screen,Epics_Cash[1],Bar)
            if ID == GrID :
                pygame.draw.rect(screen,[255,0,0],Bar)
        Epics_Cash[0] += 1
        if Epics_Cash[0] >= Len :
            Epics_Cash[0] = 0
        #pygame.draw.rect(screen,[255,255,255],[0,10,800,10],False)
    #AverageLine
    Av = 0
    Avid = 0
    global Freq_List
    for Bar in Bars :
        Avid
        Av += Bar[3]
        Avid += 1
        if len(Freq_List) >= screen.get_width()/5 :
            Freq_List = Freq_List[1:]
    Av = int(Av/Avid)
    Freq_List.append(Av)
    if Av_Aktiv :
        pygame.draw.line(screen,[0,100,0],[0,Av],[screen.get_width(),Av],3)
        GraphDraw() 
    #PeakFont
    if Pfont_Aktiv :
        font = pygame.font.SysFont("Arial",20)
        Img = font.render(str(Hfs), True,[255,255,255])
        screen.blit(Img,[700,600])

In [4]:
pygame.init()
def NextData(Cash):
    #Reurns the current Sample
    Ret = Cash[Itera[1]]
    Itera[1] += 1
    if Itera[1] == Iteralen[1]-1:
        Itera[1] = 0
    return Ret,Cash
def Update(screen,spectrum):
    #Bar ot Graph/Data
    Bars = []
    D = 0.6
    S = 1
    fs,amps = spectrum.render_full()
    ID = -1
    for PosX in fs :
        ID += 1
        if (PosX*D) < screen.get_width():
            AMPD = (amps[ID]+1)*2
            Block = 50
            if AMPD >= 700 :
                AMPD = 700
            Bars.append([PosX*D,0,5,AMPD])
    Render(screen,Bars,fs)



In [5]:
#Setup
#screen = pygame.display.set_mode([1920,1080],pygame.RESIZABLE)
screen = pygame.display.set_mode([1280,720])
#VarDef
Freq_List = []
Aktiv = True
uhr = pygame.time.Clock()
Music_Name = ""
Cash,Cash2,Meng,M_Name =sample_generator()
easygui.msgbox(str(Meng)+" Samples,Sample-duration : 0.1 sec."+",length: "+str(int(Meng/10)),"Music Data")
Cash2B = Cash2[:]
CashCopy = Cash[:]
Epics_Cash = [0,[255,255,255],[200,200,200],[10,10,100]]
Itera = [0,0]
Iteralen = [len(Cash2),len(Cash)]
#Pygame Mixer Start
M_Type = "STD"
if M_Type == "STD":
    pygame.mixer.music.load(M_Name)
    pygame.mixer.music.set_volume(1)
    pygame.mixer.music.play(-1)
#Pygame setup
screen.fill([0,0,0])
pygame.key.set_repeat(80,100)
#Feature Var
Bar_Aktiv = True
Line_Aktiv = True
Av_Aktiv = True
Pfont_Aktiv = True
KeyKill = False
Runtime = 0
Restart = False

In [6]:
#Main Loop
while Aktiv :
    #Play Music/Timer
    if M_Type == "STD":
        if not Restart:
            uhr.tick(10)
            Restart = False
        Runtime = Itera[1]/10
    screen.fill([0,0,0])
    spectrum,Cash = NextData(Cash)
    if M_Type == "SAMP":
        Cash2[Itera[0]].normalize()
        Cash2[Itera[0]].apodize()
        Cash2[Itera[0]].play
        Audio(Cash2[Itera[0]].play, autoplay=True)
        Itera[0]+=1
        Runtime = Itera[1]/10
    if Itera[0] == Iteralen[0]-1:
        Itera[0] = 0
        #Restart Music
        Restart = True
    if spectrum != None:
        Update(screen,spectrum)
    else :
        Cash = CashCopy
    if Itera[1] == 0 :
        Runtime = 0
    #Runtime-Anzeige
    font = pygame.font.SysFont("Arial",20)
    Runtime2 = int(Runtime)
    Img = font.render("Runtime(Sec): "+str(Runtime2), True,[255,255,255])
    screen.blit(Img,[1000,600])
    #Main event Loop
    pygame.display.flip()
    for event in pygame.event.get():
        if event.type == pygame.QUIT :
            Aktiv = False
        elif event.type == pygame.KEYDOWN :
            #Key Handler
            if event.key == pygame.K_b :
                Bar_Aktiv = not Bar_Aktiv
            elif event.key == pygame.K_l :
                Line_Aktiv = not Line_Aktiv
            elif event.key == pygame.K_a :
                Av_Aktiv = not Av_Aktiv
            elif event.key == pygame.K_f :
                Pfont_Aktiv = not Pfont_Aktiv
            else :
                Aktiv = False
                KeyKill = True
pygame.quit()

720 720
720 720
720 715
720 720
720 715
720 714
720 720
720 715
720 714
720 713
720 720
720 715
720 714
720 713
720 712
720 720
720 715
720 714
720 713
720 712
720 712
720 720
720 715
720 714
720 713
720 712
720 712
720 712
720 720
720 715
720 714
720 713
720 712
720 712
720 712
720 712
720 720
720 715
720 714
720 713
720 712
720 712
720 712
720 712
720 712
720 720
720 715
720 714
720 713
720 712
720 712
720 712
720 712
720 712
720 712
720 720
720 715
720 714
720 713
720 712
720 712
720 712
720 712
720 712
720 712
720 711
720 720
720 715
720 714
720 713
720 712
720 712
720 712
720 712
720 712
720 712
720 711
720 711
720 720
720 715
720 714
720 713
720 712
720 712
720 712
720 712
720 712
720 712
720 711
720 711
720 711
720 720
720 715
720 714
720 713
720 712
720 712
720 712
720 712
720 712
720 712
720 711
720 711
720 711
720 711
720 720
720 715
720 714
720 713
720 712
720 712
720 712
720 712
720 712
720 712
720 711
720 711
720 711
720 711
720 719
720 720
720 715
720 714
720 713
720 712


720 707
720 706
720 706
720 712
720 716
720 709
720 707
720 707
720 707
720 706
720 706
720 706
720 706
720 720
720 713
720 710
720 708
720 707
720 707
720 707
720 707
720 706
720 706
720 714
720 709
720 708
720 707
720 706
720 706
720 706
720 706
720 706
720 706
720 705
720 705
720 705
720 705
720 713
720 708
720 713
720 709
720 715
720 715
720 709
720 708
720 708
720 708
720 707
720 706
720 706
720 712
720 716
720 709
720 707
720 707
720 707
720 706
720 706
720 706
720 706
720 720
720 713
720 710
720 708
720 707
720 707
720 707
720 707
720 706
720 706
720 706
720 714
720 709
720 708
720 707
720 706
720 706
720 706
720 706
720 706
720 706
720 705
720 705
720 705
720 705
720 713
720 708
720 713
720 709
720 715
720 715
720 709
720 708
720 708
720 708
720 707
720 706
720 706
720 712
720 716
720 709
720 707
720 707
720 707
720 706
720 706
720 706
720 706
720 720
720 713
720 710
720 708
720 707
720 707
720 707
720 707
720 706
720 706
720 706
720 706
720 714
720 709
720 708
720 707
720 706


720 709
720 704
720 703
720 702
720 701
720 701
720 701
720 701
720 701
720 701
720 700
720 700
720 700
720 700
720 708
720 703
720 708
720 704
720 710
720 710
720 704
720 703
720 703
720 703
720 702
720 701
720 701
720 707
720 711
720 704
720 702
720 702
720 702
720 701
720 701
720 701
720 701
720 715
720 708
720 705
720 703
720 702
720 702
720 702
720 702
720 701
720 701
720 701
720 701
720 700
720 701
720 714
720 706
720 718
720 712
720 717
720 715
720 706
720 705
720 705
720 704
720 703
720 702
720 702
720 713
720 720
720 711
720 709
720 704
720 703
720 702
720 701
720 701
720 701
720 701
720 701
720 701
720 700
720 700
720 700
720 700
720 708
720 703
720 708
720 704
720 710
720 710
720 704
720 703
720 703
720 703
720 702
720 701
720 701
720 707
720 711
720 704
720 702
720 702
720 702
720 701
720 701
720 701
720 701
720 715
720 708
720 705
720 703
720 702
720 702
720 702
720 702
720 701
720 701
720 701
720 701
720 700
720 701
720 714
720 706
720 718
720 712
720 717
720 715
720 706


720 701
720 696
720 695
720 694
720 693
720 693
720 693
720 693
720 693
720 693
720 692
720 692
720 692
720 692
720 700
720 695
720 700
720 696
720 702
720 702
720 696
720 695
720 695
720 695
720 694
720 693
720 693
720 699
720 703
720 696
720 694
720 694
720 694
720 693
720 693
720 693
720 693
720 707
720 700
720 697
720 695
720 694
720 694
720 694
720 694
720 693
720 693
720 693
720 693
720 692
720 693
720 706
720 698
720 710
720 704
720 709
720 707
720 698
720 697
720 697
720 696
720 695
720 694
720 694
720 705
720 712
720 703
720 698
720 696
720 695
720 695
720 695
720 694
720 694
720 714
720 704
720 700
720 697
720 695
720 695
720 696
720 695
720 694
720 694
720 694
720 693
720 693
720 702
720 709
720 699
720 719
720 705
720 720
720 715
720 701
720 701
720 700
720 699
720 697
720 695
720 694
720 716
720 715
720 701
720 698
720 701
720 696
720 695
720 694
720 693
720 693
720 693
720 693
720 693
720 693
720 692
720 692
720 692
720 692
720 700
720 695
720 700
720 696
720 702
720 702


720 689
720 694
720 690
720 696
720 696
720 690
720 689
720 689
720 689
720 688
720 687
720 687
720 693
720 697
720 690
720 688
720 688
720 688
720 687
720 687
720 687
720 687
720 701
720 694
720 691
720 689
720 688
720 688
720 688
720 688
720 687
720 687
720 687
720 687
720 686
720 687
720 700
720 692
720 704
720 698
720 703
720 701
720 692
720 691
720 691
720 690
720 689
720 688
720 688
720 699
720 706
720 697
720 692
720 690
720 689
720 689
720 689
720 688
720 688
720 708
720 698
720 694
720 691
720 689
720 689
720 690
720 689
720 688
720 688
720 688
720 687
720 687
720 696
720 703
720 693
720 713
720 699
720 714
720 709
720 695
720 695
720 694
720 693
720 691
720 689
720 688
720 710
720 709
720 695
720 692
720 692
720 691
720 689
720 689
720 688
720 689
720 720
720 702
720 697
720 694
720 695
720 690
720 689
720 688
720 687
720 687
720 687
720 687
720 687
720 687
720 686
720 686
720 686
720 686
720 694
720 689
720 694
720 690
720 696
720 696
720 690
720 689
720 689
720 689
720 688


...

720 694
720 672
720 674
720 681
720 679
720 675
720 669
720 671
720 661
720 711
720 676
720 675
720 679
720 659
720 708
720 681
720 677
720 672
720 706
720 705
720 678
720 646
720 644
720 686
720 667
720 648
720 646
720 644
720 642
720 705
720 641
720 638
720 707
720 682
720 673
720 663
720 657
720 647
720 644
720 644
720 642
720 641
720 640
720 639
720 637
720 636
720 709
720 664
720 685
720 689
720 681
720 703
720 667
720 657
720 655
720 703
720 700
720 669
720 642
720 641
720 701
720 684
720 672
720 662
720 658
720 669
720 690
720 646
720 643
720 707
720 681
720 673
720 662
720 658
720 647
720 646
720 646
720 644
720 642
720 641
720 639
720 638
720 636
720 710
720 662
720 688
720 681
720 692
720 688
720 672
720 664
720 666
720 707
720 702
720 670
720 644
720 644
720 686
720 662
720 648
720 645
720 644
720 684
720 679
720 639
720 638
720 711
720 676
720 670
720 661
720 654
720 644
720 644
720 644
720 642
720 670
720 674
720 654
720 649
720 648
720 707
720 669
720 686
720 683
720 694


720 669
720 671
720 661
720 711
720 676
720 675
720 679
720 659
720 708
720 681
720 677
720 672
720 706
720 705
720 678
720 646
720 644
720 686
720 667
720 648
720 646
720 644
720 642
720 705
720 641
720 638
720 707
720 682
720 673
720 663
720 657
720 647
720 644
720 644
720 642
720 641
720 640
720 639
720 637
720 636
720 709
720 664
720 685
720 689
720 681
720 703
720 667
720 657
720 655
720 703
720 700
720 669
720 642
720 641
720 701
720 684
720 672
720 662
720 658
720 669
720 690
720 646
720 643
720 707
720 681
720 673
720 662
720 658
720 647
720 646
720 646
720 644
720 642
720 641
720 639
720 638
720 636
720 710
720 662
720 688
720 681
720 692
720 688
720 672
720 664
720 666
720 707
720 702
720 670
720 644
720 644
720 686
720 662
720 648
720 645
720 644
720 684
720 679
720 639
720 638
720 711
720 676
720 670
720 661
720 654
720 644
720 644
720 644
720 642
720 670
720 674
720 654
720 649
720 648
720 707
720 669
720 686
720 683
720 694
720 695
720 670
720 658
720 652
720 720
720 710


720 679
720 659
720 708
720 681
720 677
720 672
720 706
720 705
720 678
720 646
720 644
720 686
720 667
720 648
720 646
720 644
720 642
720 705
720 641
720 638
720 707
720 682
720 673
720 663
720 657
720 647
720 644
720 644
720 642
720 641
720 640
720 639
720 637
720 636
720 709
720 664
720 685
720 689
720 681
720 703
720 667
720 657
720 655
720 703
720 700
720 669
720 642
720 641
720 701
720 684
720 672
720 662
720 658
720 669
720 690
720 646
720 643
720 707
720 681
720 673
720 662
720 658
720 647
720 646
720 646
720 644
720 642
720 641
720 639
720 638
720 636
720 710
720 662
720 688
720 681
720 692
720 688
720 672
720 664
720 666
720 707
720 702
720 670
720 644
720 644
720 686
720 662
720 648
720 645
720 644
720 684
720 679
720 639
720 638
720 711
720 676
720 670
720 661
720 654
720 644
720 644
720 644
720 642
720 670
720 674
720 654
720 649
720 648
720 707
720 669
720 686
720 683
720 694
720 695
720 670
720 658
720 652
720 720
720 710
720 667
720 650
720 648
720 700
720 675
720 671


720 706
720 705
720 678
720 646
720 644
720 686
720 667
720 648
720 646
720 644
720 642
720 705
720 641
720 638
720 707
720 682
720 673
720 663
720 657
720 647
720 644
720 644
720 642
720 641
720 640
720 639
720 637
720 636
720 709
720 664
720 685
720 689
720 681
720 703
720 667
720 657
720 655
720 703
720 700
720 669
720 642
720 641
720 701
720 684
720 672
720 662
720 658
720 669
720 690
720 646
720 643
720 707
720 681
720 673
720 662
720 658
720 647
720 646
720 646
720 644
720 642
720 641
720 639
720 638
720 636
720 710
720 662
720 688
720 681
720 692
720 688
720 672
720 664
720 666
720 707
720 702
720 670
720 644
720 644
720 686
720 662
720 648
720 645
720 644
720 684
720 679
720 639
720 638
720 711
720 676
720 670
720 661
720 654
720 644
720 644
720 644
720 642
720 670
720 674
720 654
720 649
720 648
720 707
720 669
720 686
720 683
720 694
720 695
720 670
720 658
720 652
720 720
720 710
720 667
720 650
720 648
720 700
720 675
720 671
720 668
720 658
720 678
720 669
720 647
720 649


720 664
720 645
720 643
720 641
720 639
720 702
720 638
720 635
720 704
720 679
720 670
720 660
720 654
720 644
720 641
720 641
720 639
720 638
720 637
720 636
720 634
720 633
720 706
720 661
720 682
720 686
720 678
720 700
720 664
720 654
720 652
720 700
720 697
720 666
720 639
720 638
720 698
720 681
720 669
720 659
720 655
720 666
720 687
720 643
720 640
720 704
720 678
720 670
720 659
720 655
720 644
720 643
720 643
720 641
720 639
720 638
720 636
720 635
720 633
720 707
720 659
720 685
720 678
720 689
720 685
720 669
720 661
720 663
720 704
720 699
720 667
720 641
720 641
720 683
720 659
720 645
720 642
720 641
720 681
720 676
720 636
720 635
720 708
720 673
720 667
720 658
720 651
720 641
720 641
720 641
720 639
720 667
720 671
720 651
720 646
720 645
720 704
720 666
720 683
720 680
720 691
720 692
720 667
720 655
720 649
720 717
720 707
720 664
720 647
720 645
720 697
720 672
720 668
720 665
720 655
720 675
720 666
720 644
720 646
720 710
720 674
720 670
720 662
720 653
720 644


In [7]:
if KeyKill :
    easygui.msgbox("Killed by KeyInterupt","System Shutdown")